# Exploratory Data Analysis

In [4]:
import wandb
import pandas as pd

wandb.login()
run = wandb.init(
    project="nyc_airbnb",
    group="eda",
    save_code=True
)
local_path = wandb.use_artifact("sample.csv:latest").file()
df = pd.read_csv(local_path)

/home/eoink/miniconda3/envs/mlflow-6f02ff4842fbe0d4c84a3c2da9d0eede237ec11e/lib/python3.12/site-packages/pydantic/_internal/_generate_schema.py:2249: UnsupportedFieldAttributeWarning: The 'repr' attribute with value False was provided to the `Field()` function, which has no effect in the context it was used. 'repr' is field-specific metadata, and can only be attached to a model field using `Annotated` metadata or by assignment. This may have happened because an `Annotated` type alias using the `type` statement was used, or if the `Field()` function was attached to a single member of a union type.
  warnings.warn(
/home/eoink/miniconda3/envs/mlflow-6f02ff4842fbe0d4c84a3c2da9d0eede237ec11e/lib/python3.12/site-packages/pydantic/_internal/_generate_schema.py:2249: UnsupportedFieldAttributeWarning: The 'frozen' attribute with value True was provided to the `Field()` function, which has no effect in the context it was used. 'frozen' is field-specific metadata, and can only be attached to a m

After loading our artifact from W&B we use `y`

In [7]:
import ydata_profiling

profile = ydata_profiling.ProfileReport(df)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 16/16 [00:00<00:00, 20.35it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

We notice:
- Missing values in several columns
- The column `last_review` is stored as a string instead of a datetime
- Outliers in the `price` column, including zeroes and extreme highs

We will apply two fixes. Missing values will be handled later in the inference pipeline so that the system can manage them at prediction time.

In [8]:
# drop outliers
min_price=10
max_price=350
idx = df['price'].between(min_price, max_price)
df = df[idx].copy()

# convert last_review to datetime
df['last_review'] = pd.to_datetime(df['last_review'])

We quickly verify our fixes

In [9]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 19001 entries, 0 to 19999
Data columns (total 16 columns):
 #   Column                          Non-Null Count  Dtype         
---  ------                          --------------  -----         
 0   id                              19001 non-null  int64         
 1   name                            18994 non-null  object        
 2   host_id                         19001 non-null  int64         
 3   host_name                       18993 non-null  object        
 4   neighbourhood_group             19001 non-null  object        
 5   neighbourhood                   19001 non-null  object        
 6   latitude                        19001 non-null  float64       
 7   longitude                       19001 non-null  float64       
 8   room_type                       19001 non-null  object        
 9   price                           19001 non-null  int64         
 10  minimum_nights                  19001 non-null  int64         
 11  number_

In [10]:
max(df['price'])

350

In [11]:
min(df['price'])

10

With our fixes in place, and their changes verifed, we have completed our EDA. We can now end the run and close our notebook.

In [12]:
run.finish()